In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175 False datasets/mgtv results/mgtv-results_internlm_best.csv


In [6]:
%%time
!python --version
!pip show flash-attn transformers torch

Python 3.11.9
Name: transformers
Version: 4.41.2
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: llamafactory, peft, trl, vllm
---
Name: torch
Version: 2.3.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, nvidia-cublas-

In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [8]:
adapter_name_or_path

'llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175'

In [9]:
%%time

model, tokenizer = load_model(adapter_name_or_path, using_llama_factory=False)

loading model: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175 with adapter: None


/home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

Some parameters are on the meta device device because they were offloaded to the cpu.
/home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages/torch/nn/modules/module.py:2047: UserWarning: for model.layers.20.attention.wqkv.lora_A.default.weight: copying from a non-meta parameter in the checkpoint to a meta parameter in the current model, which is a no-op. (Did you mean to pass `assign=True` to assign items in the state dictionary to their corresponding key in the module instead of copying them in place?)
  warnings.warn(f'for {key}: copying from a non-meta parameter in the checkpoint to a meta '
/home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages/torch/nn/modules/module.py:2047: UserWarning: for model.layers.20.attention.wqkv.lora_B.default.weight: copying from a non-meta parameter in the checkpoint to a meta parameter in the current model, which is a no-op. (Did you mean to pass `assign=True` to assign items in the state dictionary to their corr

CPU times: user 32 s, sys: 1min 18s, total: 1min 50s
Wall time: 12min


In [13]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [15]:
print_row_details(datasets["test"].to_pandas(), [1000])

--------------------------------------------------
text: 哭泣和村庄有关系吗
--------------------------------------------------
label: 是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 甄庄哭声
--------------------------------------------------
puzzle: 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。
--------------------------------------------------
truth: 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。
--------------------------------------------------
train_text: <s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是

In [16]:
%%time

prompt1 = datasets["test"]["prompt"][1000]

gen_kwargs = {"max_length": 4096, "do_sample": True, "top_k": 1}
with torch.no_grad():
    inputs = tokenizer(
        [prompt1],
        return_tensors="pt",
    ).to(device)
    outputs = model.generate(**inputs, **gen_kwargs)
    outputs = outputs[:, inputs['input_ids'].shape[1]:]
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))

NotImplementedError: Cannot copy out of meta tensor; no data!

In [12]:
adapter_name_or_path = "inflaton-ai/InternLM_2_5-7b_LoRA-r2"

model.push_to_hub(adapter_name_or_path)
tokenizer.push_to_hub(adapter_name_or_path)

/home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages/transformers/integrations/peft.py:399: FutureWarning: The `active_adapter` method is deprecated and will be removed in a future version.
  warnings.warn(
/home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


RuntimeError: The weights trying to be saved contained shared tensors [{'base_model.model.model.layers.14.attention.wo.lora_A.weight', 'base_model.model.model.layers.26.attention.wo.lora_B.weight', 'base_model.model.model.layers.3.attention.wqkv.lora_A.weight', 'base_model.model.model.layers.2.feed_forward.w3.lora_A.weight', 'base_model.model.model.layers.4.feed_forward.w1.lora_A.weight', 'base_model.model.model.layers.30.attention.wo.lora_A.weight', 'base_model.model.model.layers.14.attention.wqkv.lora_A.weight', 'base_model.model.model.layers.21.attention.wqkv.lora_A.weight', 'base_model.model.model.layers.23.feed_forward.w2.lora_B.weight', 'base_model.model.model.layers.10.feed_forward.w1.lora_A.weight', 'base_model.model.model.layers.31.attention.wo.lora_A.weight', 'base_model.model.model.layers.27.feed_forward.w2.lora_B.weight', 'base_model.model.model.layers.1.feed_forward.w3.lora_A.weight', 'base_model.model.model.layers.5.attention.wo.lora_B.weight', 'base_model.model.model.lay

In [ ]:
del model, tokenizer

In [ ]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
# model, tokenizer = load_model("inflaton-ai/InternLM_2_5-7b_LoRA-Adapter", using_llama_factory=False)

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

adapter_config.json:   0%|          | 0.00/679 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

CPU times: user 3.06 s, sys: 5.04 s, total: 8.11 s
Wall time: 31.6 s


In [ ]:
def evaluate_model(model, tokenizer, model_name, dataset):
    print(f"Evaluating model: {model_name} on {device}")
    predictions = eval_model(model, tokenizer, dataset, device=device)

    save_results(
        model_name,
        results_path,
        dataset,
        predictions,
        debug=False,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=False)
    print(metrics)

/Users/inflaton/anaconda3/envs/logical-reasoning/lib/python3.11/site-packages/transformers/generation/utils.py:1513: UserWarning: The operator 'aten::isin.Tensor_Tensor_out' is not currently supported on the MPS backend and will fall back to run on the CPU. This may have performance implications. (Triggered internally at /Users/runner/work/pytorch/pytorch/pytorch/aten/src/ATen/mps/MPSFallback.mm:13.)
  if eos_token_id is not None and torch.isin(elements=eos_token_id, test_elements=pad_token_id).any():


是
CPU times: user 579 ms, sys: 330 ms, total: 909 ms
Wall time: 2.86 s


In [ ]:
%%time

evaluate_model(model, tokenizer, f"{model_name}_{adapter_name_or_path}_nv4080", datasets["test"])